# Markov models for ion channels
Ion channels are proteins with different conformations. The transition between those can be described as a discrete state, continuous time Markov model. See the [script](https://itb.biologie.hu-berlin.de/~schleimer/doc/script_biomath.html#the-continuum-limit-of-a-membrane-patch) for some more detail.

To start download a [json]() file that has some channel definitions in it and place it in the directory with this notebook. Load it and construct a directed graph object.

Note that the brian2 unit system is used.

In [ ]:
import json, networkx, pygraphviz, brian2
units=dict( list(vars(brian2.units).items()) + list(vars(brian2.units.allunits).items()) )
db = json.load(open("./chanlib.json"))
print "Ion channels: {}".format(db.keys())

Let's look at the K$^+$ channel, called delayed rectifier. Assume that the voltage dependent closing rate is denoted by $a(v)$ and the opening rate is $b(v)$.

In [ ]:
from networkx.readwrite import json_graph
G = networkx.DiGraph(json_graph.node_link_graph(db['K_dr']['graph']))
Gviz=networkx.nx_agraph.to_agraph(G)
Gviz.layout('circo')
Gviz.draw('G.svg')
from IPython.display import SVG, display
display(SVG('G.svg'))

Master equations describe the evolution of occupancy probabilities

$\dot{\vec p}=\boldsymbol Q(v)\vec p$,

with $\boldsymbol Q$ the [transition rate matrix](https://en.wikipedia.org/wiki/Transition_rate_matrix).

To simulate a [sample path](https://en.wikipedia.org/wiki/Stochastic_process#Sample_function), algorithms such as Gillespie's stochastic simmulation algorithm can be employed.

The infinitesimal transition matrix can be extracted from the graph.

## Gillespie's SSA

Let us simulate a membrane patch with one K$^+$ channel in _voltage clamp_. The formulation of the algorithm uses the The propensity function describes the probablity of the next event to occure given the current species and state values. The necessary information can be extracted from the graph. We need species, rates and the [incidence matrix](https://en.wikipedia.org/wiki/Incidence_matrix), $\boldsymbol N\in\mathbb R^{n\times m}$, that maps species to reactions. Here $n$ is the number of species and $m$ is the number of reactions. The entries of the incidence matrix shows a -1 if the reaction decreases this speces and an +1 if it increases it (in sysbio $\boldsymbol N$ is also called [stochiometry matrix](https://en.wikipedia.org/wiki/Stoichiometry#Stoichiometry_matrix)). Conservation of species requires that collumnts sum to zero.

In [ ]:
import sympy
rates = [sympy.S(k['label']) for i,j,k, in networkx.to_edgelist(G)]
species = [sympy.S(k) for k in G.nodes()]
N_mat = networkx.incidence_matrix(G,oriented=1).toarray()
print species, rates, N_mat

Propensities are obtained by the mass action law.

In [ ]:
import scipy
fromreacts = scipy.zeros(N_mat.shape)
fromreacts[N_mat<0] = 1
propensities = scipy.dot(species,fromreacts) * rates
print "Check the propensities from the graph: ", propensities

The algorithm is as follows, the formal derivation is here.

~~~
while
  r1 = rand(0,1)
  r2 = rand(0,1)
  t_react = -log(r1) // next reaction time
~~~

In [ ]:
%matplotlib inline
from matplotlib import pyplot
v = scipy.linspace(-100,20,300) * eval("mV",units)
actfoo=sympy.lambdify("v", str(sympy.S("a/(a+b)").subs(db['K_dr']['foo'])),units)
taufoo=sympy.lambdify("v", str(sympy.S("1/(a+b)").subs(db['K_dr']['foo'])),units)
pyplot.subplot(121)
pyplot.plot(v/brian2.mV,[actfoo(k) for k in v])
pyplot.xlabel('v [mV]')
pyplot.ylabel('p(open)')
pyplot.subplot(122)
pyplot.plot(v/brian2.mV,[taufoo(k)/brian2.ms for k in v])
pyplot.xlabel('v [mV]')
pyplot.ylabel('time const')
pyplot.tight_layout()

One can chose an intersting voltage range to look at the clamped channels.

In [ ]:
# Gillespie's SSA algorithm
def ssa(propensity,N,tmax,species):
    t=0
    tspecies = scipy.array(species,int)
    ix= scipy.arange(N.shape[1],dtype=scipy.int16)
    while(t<tmax):
        prop = propensity(*tspecies)
        cprop = scipy.cumsum(prop) * eval(repr(prop[0].dim),units)
        tau = -scipy.log(scipy.rand()) / cprop[-1] # next reaction time
        j = (ix[ cprop > (scipy.rand() * cprop[-1]) ])[0] # next reaction
        t = t + tau
        tspecies = tspecies + N[:,j]
        yield t,tspecies

In [ ]:
# this is clamped to -40 mV, but you can test other voltages
propensityfoo = sympy.lambdify(species,[k.subs(db['K_dr']['foo']).subs({'v':"-40*mV"}) for k in propensities],units)
tmax = eval("100*ms",units)
t,path = zip(*[(i,j) for i,j in ssa(propensityfoo,scipy.array(N_mat,int),tmax,[155,185,99,12,49])])
t = scipy.asfarray(t)
path = scipy.asfarray(path)

In [ ]:
species.index(sympy.S("o"))
pyplot.plot(t,path[:,species.index(sympy.S("o"))])
pyplot.title("SSA timecourse")
pyplot.xlabel("time [seconds]")
pyplot.ylabel("Number of open channels $o$")

The current in a voltage clamped membrane would be $I = \gamma o(E-v)$, where $\gamma$ is the unitary conductance, $E$ the Nernst potential and $v$ voltage. All but $o$ is a constant factor.
To look at the spectral properties, resample the unevenly sampled time series.

In [ ]:
# resammple to regular grid
from scipy import interpolate
dt = eval("0.1 * ms",units)
ix_open = species.index(sympy.S("o"))
tbin = scipy.arange(tmax//dt) * dt
obin = interpolate.griddata(t,path[:,ix_open],tbin)

In [ ]:
# just checking
pyplot.plot(tbin,obin)
pyplot.title("SSA timecourse")
pyplot.xlabel("time [seconds]")
pyplot.ylabel("Number of open channels $o$")

In [ ]:
from scipy.signal import welch
f, Pxx = welch(obin[1:],fs=1./float(dt),nfft=2**12)
pyplot.loglog(f,Pxx)
pyplot.xlabel("frequency [Hz]")
pyplot.ylabel("Power spectral density")

## Diffusion approximations
An alternative to generate sample paths is to derive an diffusion approximation. In the script the proposed method used Ornstein-Uhlenbeck processes that show the same correlation structure as the Markov model. We define the infinitesimal $\boldsymbol Q$ matrix as

In [ ]:
Q=scipy.array([[sympy.S(i) if i else 0 for i in j] for j in networkx.attr_matrix(G,edge_attr='label',dtype='S1024')[0].tolist()])
Q=sympy.Matrix(Q-scipy.diag(Q.sum(1))) # invenitesimal Q matrix
Q

In [ ]:
l,dummy,L=zip(*Q.T.eigenvects()) # left/right eigensystem
L=sympy.Matrix([sympy.flatten(k[0]) for k in L]).T
r,dummy,R=zip(*Q.eigenvects()) # left/right eigensystem
R=sympy.Matrix([sympy.flatten(k[0]) for k in R]).T
# normalise
D=[[sympy.simplify(i) for i in j] for j in (L.T*R).tolist()]
for i in range(len(D)):
    R[:,i]/=D[i][i]
    
sig2=[sympy.factor(sympy.simplify((L[:,j]*R[:,j].T)[ix_open,ix_open])) for j in range(len(l))]

Checkout [this](http://journals.plos.org/ploscompbiol/article?id=10.1371/journal.pcbi.1001102) fee and open article about diffusion approximating ion channel noise. Compare `sig2` and `l` to the parameters of the OU process derived in this article.

In [ ]:
print l
print sig2

# Simulating SDEs with brian2

In [ ]:
sde=brian2.Equations("v : volt")
for i,(j,k) in enumerate(zip(l,sig2)):
    if j != 0:
        rhsstr = "-1*({1})*n{0}+sqrt(2*({2})/({1}))*xi_{0}".format(i,j,k)
        rhsstr = str(sympy.S(rhsstr).simplify().subs(db['K_dr']['foo']))
        sde += brian2.Equations("dn{0}/dt = {1} : 1".format(i,rhsstr))

In [ ]:
G = brian2.NeuronGroup(1, model=sde, method="heun")

# state init
G.v = eval("-40 * mV", units)
duration = eval("100 * ms",units)

# states = brian2.StateMonitor(G, sde.eq_names, record=True)
states = brian2.StateMonitor(G, sde.eq_names, record=True)
net = brian2.Network(G,states)
net.run(duration)

[Here](http://journals.plos.org/plosone/article?id=10.1371/journal.pone.0036670) is an other diffusion approximation. What is the difference? Can we also derive the equations from the graph? Why are there more than one diffusion approximations to a Master equation?